In [ ]:
!pip install pandas, annoy, transformers, sentence_transformers

In [ ]:
from datetime import datetime

import os
import sqlite3

from sentence_transformers import SentenceTransformer
import numpy as np
from annoy import AnnoyIndex
from transformers import pipeline

In [11]:
dbpath = os.path.join("database", "rss_feed.db")

In [12]:
class Database:
    def __init__(self, db_path):
        """Initialize the database connection."""
        self.db_path = db_path

    def connect(self):
        """Create and return a new database connection."""
        return sqlite3.connect(self.db_path)

    def execute_query(self, query, params=None):
        """Execute a query with optional parameters."""
        params = params or ()
        with self.connect() as conn:
            cursor = conn.cursor()
            cursor.execute(query, params)
            conn.commit()

    def fetch_all(self, query, params=None):
        """Fetch all rows for a given query."""
        params = params or ()
        with self.connect() as conn:
            cursor = conn.cursor()
            cursor.execute(query, params)
            return cursor.fetchall()

    def fetch_one(self, query, params=None):
        """Fetch a single row for a given query."""
        params = params or ()
        with self.connect() as conn:
            cursor = conn.cursor()
            cursor.execute(query, params)
            return cursor.fetchone()


In [ ]:
db = Database(dbpath)

In [34]:
create_interaction_table_query = '''
CREATE TABLE IF NOT EXISTS user_interactions (
    interaction_id INTEGER PRIMARY KEY AUTOINCREMENT,
    block_id INTEGER NOT NULL,
    block_type TEXT NOT NULL,
    action TEXT NOT NULL,
    timestamp TEXT NOT NULL
)
'''

db.execute_query(create_interaction_table_query)

In [ ]:

def log_user_interaction(block_id, block_type, action):
    # Prepare the interaction data
    timestamp = datetime.now().isoformat()
    query = '''
    INSERT INTO user_interactions (block_id, block_type, action, timestamp)
    VALUES (?, ?, ?, ?)
    '''
    db.execute_query(query, (block_id, block_type, action, timestamp))

# Example usage:
log_user_interaction(1, "article", "view")

In [32]:
# Fetch a single article by ID
articles = db.fetch_all('SELECT * FROM user_interactions')
for a in articles:
    print(a)

(1, 1550, 'article', 'thumbs_up', '2024-11-27T10:19:13.686003')
(2, 1516, 'article', 'next', '2024-11-27T10:19:13.695976')
(3, 1516, 'article', 'thumbs_up', '2024-11-27T10:19:14.896072')


In [16]:
create_articles_table_query = '''
CREATE TABLE IF NOT EXISTS articles (
    article_id INTEGER PRIMARY KEY AUTOINCREMENT,
    title TEXT NOT NULL,
    description TEXT,
    link TEXT UNIQUE,
    category TEXT,
    published_date TEXT
)
'''
db.execute_query(create_articles_table_query)

In [21]:
# Fetch all articles
select_query = 'SELECT * FROM articles'
articles = db.fetch_all(select_query)
for article in articles:
    print(article)

(1, 'The Mom of the Troublemaking Child Finally Intervened. Uh, That Was Not At All What We Had in Mind. - Slate', 'The other parents are not taking this well.', 'https://slate.com/advice/2024/11/problem-child-intervention-play-parenting-advice.html', 'Lifestyle', '2024-11-25T11:00:00Z', 'Slate Plus members get more Care and Feeding every week. Have a question about kids, parenting, or family life? Submit it here!\n\nDear Care and Feeding,\n\nI live in a small, isolated town where my 2-year-old daughter and another 2-and-a-half-year-old, “Vanessa,” are among the few young children. Vanessa has developed concerning behaviors—hitting and shoving other kids when she wants toys or space. Her mother “Cara,” who had a difficult Soviet upbringing, has admitted she struggles with discipline and often seeks my advice.\n\nRecently, Cara has started intervening more—which is great!—but her approach is problematic. When Vanessa pushes kids or grabs toys, instead of addressing the aggressive behavi

In [33]:
# Drop the existing articles table if it exists
drop_articles_table_query = '''
DROP TABLE IF EXISTS user_interactions
'''
db.execute_query(drop_articles_table_query)
